### authorize natural language api

In [0]:
from google.cloud import language
from google.cloud.language import enums
from google.cloud.language import types
from google.cloud import storage
import pandas as pd
import re
import os
from nltk.tokenize import WordPunctTokenizer
!pip install gcsfs

In [0]:
#upload the credential for API call
from google.colab import files
uploaded = files.upload()

Saving MLCloudTwitter-fb0c476d2985.json to MLCloudTwitter-fb0c476d2985.json


In [0]:
!export GOOGLE_APPLICATION_CREDENTIALS="MLCloudTwitter-fb0c476d2985.json"
!gcloud auth activate-service-account --key-file "MLCloudTwitter-fb0c476d2985.json"

Activated service account credentials for: [jac-333@mlcloudtwitter.iam.gserviceaccount.com]


In [0]:
os.environ["GOOGLE_APPLICATION_CREDENTIALS"]="MLCloudTwitter-fb0c476d2985.json"

#### ingest data


In [0]:
twt = pd.read_csv('gs://mlcloudtwitter/fake_meat_tweets_clean.csv')
twt.head()

Unnamed: 0  ...  search_key_word
0           0  ...  artificial meat
1           1  ...  artificial meat
2           2  ...  artificial meat
3           3  ...  artificial meat
4           4  ...  artificial meat

[5 rows x 11 columns]

In [0]:
def clean_tweets(tweet):
    user_removed = re.sub(r'@[A-Za-z0-9]+','',tweet)
    link_removed = re.sub('https?://[A-Za-z0-9./]+','',user_removed)
    number_removed = re.sub('[^a-zA-Z]', ' ', link_removed)
    lower_case_tweet= number_removed.lower()
    tok = WordPunctTokenizer()
    words = tok.tokenize(lower_case_tweet)
    clean_tweet = (' '.join(words)).strip()
    return clean_tweet


def analyze_row_score(tweet):
  """Run a sentiment analysis request on text within a passed row."""
  try:
    client = language.LanguageServiceClient()
    tweet_cleaned=clean_tweets(tweet)
    document = types\
              .Document(content=tweet_cleaned,
                        type=enums.Document.Type.PLAIN_TEXT)
    sentiment_score = client\
                      .analyze_sentiment(document=document)\
                      .document_sentiment\
                      .score
  except Exception:
    print("Size exceeded sentiment:  Fail")
    return None
  return sentiment_score

def analyze_row_magnitude(tweet):
  """Run a sentiment analysis request on text within a passed row."""
  try:
    client = language.LanguageServiceClient()
    tweet_cleaned=clean_tweets(tweet)
    document = types\
              .Document(content=tweet_cleaned,
                        type=enums.Document.Type.PLAIN_TEXT)
    magnitude = client\
                      .analyze_sentiment(document=document)\
                      .document_sentiment\
                      .magnitude
  except Exception:
    print("Size exceeded magnitude:  Fail")
    return None
  return magnitude

def apply_senti_mag(df, column="tweet"):
    """Uses Pandas Apply to Create Sentiment Analysis"""
    df['Sentiment'] = df[column].apply(analyze_row_score)
    df['Magnitude'] = df[column].apply(analyze_row_magnitude)
    return df


In [0]:
rating1_senti= apply_senti_mag(twt)
rating1_senti.head()

Size exceeded sentiment:  Fail
Size exceeded sentiment:  Fail
Size exceeded sentiment:  Fail
Size exceeded sentiment:  Fail
Size exceeded sentiment:  Fail
Size exceeded sentiment:  Fail
Size exceeded sentiment:  Fail
Size exceeded sentiment:  Fail
Size exceeded sentiment:  Fail
Size exceeded sentiment:  Fail
Size exceeded sentiment:  Fail
Size exceeded sentiment:  Fail
Size exceeded sentiment:  Fail
Size exceeded sentiment:  Fail
Size exceeded sentiment:  Fail
Size exceeded sentiment:  Fail
Size exceeded sentiment:  Fail
Size exceeded sentiment:  Fail
Size exceeded sentiment:  Fail
Size exceeded sentiment:  Fail
Size exceeded sentiment:  Fail
Size exceeded sentiment:  Fail
Size exceeded sentiment:  Fail
Size exceeded magnitude:  Fail
Size exceeded magnitude:  Fail
Size exceeded magnitude:  Fail
Size exceeded magnitude:  Fail
Size exceeded magnitude:  Fail
Size exceeded magnitude:  Fail
Size exceeded magnitude:  Fail
Size exceeded magnitude:  Fail
Size exceeded magnitude:  Fail
Size exc

Unnamed: 0  Unnamed: 0.1  ...  Sentiment  Magnitude
0           0             0  ...       -0.5        0.5
1           1             1  ...       -0.8        0.8
2           2             2  ...        0.1        0.1
3           3             3  ...       -0.7        0.7
4           4             4  ...        0.0        0.0

[5 rows x 13 columns]

In [0]:
#export the file to save the result
client = storage.Client()
bucket = client.get_bucket('mlcloudtwitter')
bucket.blob('fake_meat_tweets_sentiment.csv').upload_from_string(rating1_senti.to_csv(), 'text/csv')

### plot raw result 


In [0]:
#read from saved result 
rating1_senti = pd.read_csv('gs://mlcloudtwitter/fake_meat_tweets_sentiment.csv')
rating1_senti.head()

Unnamed: 0  Unnamed: 0.1  ...  Sentiment  Magnitude
0           0             0  ...       -0.5        0.5
1           1             1  ...       -0.8        0.8
2           2             2  ...        0.1        0.1
3           3             3  ...       -0.7        0.7
4           4             4  ...        0.0        0.0

[5 rows x 14 columns]

In [0]:

def analyze_result(senti):
    if senti <= -0.1:
        status = 'NEGATIVE ❌'
    elif senti <= 0.1:
        status = 'NEUTRAL ?'
    else:
        status = 'POSITIVE ✅'
    return status

In [0]:
rating1_senti['senti_result']=rating1_senti['Sentiment'].apply(analyze_result)
rating1_senti.head()


Unnamed: 0  Unnamed: 0.1  Unnamed: 0.1.1  ...  Sentiment  Magnitude senti_result
0           0             0               0  ...       -0.5        0.5   NEGATIVE ❌
1           1             1               1  ...       -0.8        0.8   NEGATIVE ❌
2           2             2               2  ...        0.1        0.1   POSITIVE ✅
3           3             3               3  ...       -0.7        0.7   NEGATIVE ❌
4           4             4               4  ...        0.0        0.0    NEUTRAL ?

[5 rows x 15 columns]

In [0]:
# Overall sentiment category
import altair as alt
alt.Chart(rating1_senti).mark_bar(size=30).encode(
  x=alt.X('senti_result',title='Sentiment Label'),
  y=alt.Y('count(senti_result)',title='Number of Twitter'),
  color='senti_result'
).properties(width=200)

alt.Chart(...)

In [0]:
# histogram to see sentiment
import altair as alt
alt.Chart(rating1_senti).mark_bar().encode(
  x=alt.X('Sentiment',title='Sentiment Score',bin=alt.Bin(step=0.1)),
  y=alt.Y('count()',title='Number of Twitter'),
  color='senti_result'
)

alt.Chart(...)

### Aggregate by date

In [0]:
#group by date
rating1_senti_agg = rating1_senti.groupby(by='date',as_index=False).mean()
rating1_senti_agg

date   Unnamed: 0  Unnamed: 0.1  ...       user_id  Sentiment  Magnitude
0   2020-02-18  1940.000000   1940.000000  ...  3.057435e+17  -0.060177   0.322124
1   2020-02-19  1873.000000   1873.000000  ...  2.501507e+17  -0.157143   0.338095
2   2020-02-20  1853.000000   1853.000000  ...  2.689667e+17   0.005263   0.278947
3   2020-02-21  1834.000000   1834.000000  ...  7.335390e+17   0.094737   0.273684
4   2020-02-22  1820.500000   1820.500000  ...  6.826642e+17   0.187500   0.462500
..         ...          ...           ...  ...           ...        ...        ...
74  2020-05-02  1599.784314   1599.784314  ...  3.239246e+17  -0.233333   0.464706
75  2020-05-03  1371.048387   1371.048387  ...  4.717859e+17  -0.275806   0.433871
76  2020-05-04   992.326531    992.326531  ...  4.775565e+17  -0.367347   0.440816
77  2020-05-05  1550.735294   1550.735294  ...  5.244958e+17  -0.258824   0.467647
78  2020-05-06  2374.162041   2374.162041  ...  4.079964e+17  -0.018784   0.407895

[79 rows x 9 columns]

In [0]:
rating1_senti_agg['senti_result']=rating1_senti_agg['Sentiment'].apply(analyze_result)
rating1_senti_agg.head()

date  Unnamed: 0  Unnamed: 0.1  ...  Sentiment  Magnitude  senti_result
0  2020-02-18      1940.0        1940.0  ...  -0.060177   0.322124     NEUTRAL ?
1  2020-02-19      1873.0        1873.0  ...  -0.157143   0.338095    NEGATIVE ❌
2  2020-02-20      1853.0        1853.0  ...   0.005263   0.278947     NEUTRAL ?
3  2020-02-21      1834.0        1834.0  ...   0.094737   0.273684     NEUTRAL ?
4  2020-02-22      1820.5        1820.5  ...   0.187500   0.462500    POSITIVE ✅

[5 rows x 10 columns]

In [0]:
#sentiment and magnitude by date
bar=alt.Chart(rating1_senti_agg).mark_bar(size=10).encode(
  x='date',
  y='Sentiment',
  color='Magnitude'
).properties(width=900)

rule = alt.Chart(rating1_senti_agg).mark_rule(color='red').encode(
    y='mean(Sentiment)'
)

(bar + rule).properties(width=900)

alt.LayerChart(...)

#### Appendix  - two more plots


In [0]:
# Overall sentiment category by date
import altair as alt
alt.Chart(rating1_senti_agg).mark_bar(size=30).encode(
  x=alt.X('senti_result',title='Sentiment Label'),
  y=alt.Y('count(senti_result)',title='Number of days'),
  color='senti_result'
).properties(width=200)


alt.Chart(...)

In [0]:
rating1_senti_agg.groupby(by='senti_result',as_index=False).count()

senti_result  date  Unnamed: 0  ...  user_id  Sentiment  Magnitude
0   NEGATIVE ❌    27          27  ...       27         27         27
1    NEUTRAL ?    48          48  ...       48         48         48
2   POSITIVE ✅     4           4  ...        4          4          4

[3 rows x 9 columns]

In [0]:
# histogram to see sentiment by date
import altair as alt
alt.Chart(rating1_senti_agg).mark_bar().encode(
  x=alt.X('Sentiment',title='Sentiment Score',bin=alt.Bin(step=0.05)),
  y=alt.Y('count()',title='Number of Twitter'),
  color='senti_result'
)

alt.Chart(...)